### Data Preparation

In [ ]:
# Import pandas for data analysis
import pandas as pd

df  = pd.read_csv("/content/Merged_data_QA.csv")
df.head() #show first five rows

Questions  \
0        What does it mean to have a mental illness?   
1                    Who does mental illness affect?   
2                        What causes mental illness?   
3  What are some of the warning signs of mental i...   
4            Can people with mental illness recover?   

                                             Answers  
0  Mental illnesses are health conditions that di...  
1  It is estimated that mental illness affects 1 ...  
2  It is estimated that mental illness affects 1 ...  
3  Symptoms of mental health disorders vary depen...  
4  When healing from mental illness, early identi...

In [ ]:
df.shape # 118 rows | 2 cols

(118, 2)

In [ ]:
len(df.Questions)

118

In [ ]:
len(df.Answers)

118

In [ ]:
!pip install cleantext

In [ ]:
# Function to clean text data by removing unwanted characters and formatting
import cleantext

def clean(textdata):
  '''Use the cleantext library to remove extra spaces, lowercase the text,
        and remove numbers and punctuation'''
    cleaned_text = []
    for i in textdata:
        cleaned_text.append(cleantext.clean(str(i), extra_spaces=True, lowercase=True, stopwords=False, stemming=False, numbers=True, punct=True, clean_all = True))

    return cleaned_text

In [ ]:
# Apply the clean function to the questions and answers columns

df.Questions = list(clean(df.Questions))
df.Answers = list(clean(df.Answers))

In [ ]:
# Save the cleaned data into a new CSV file & save
df.to_csv("cleaned_QA_data.csv", index=False)

### GPT-2 Model

In [2]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 474.3/474.3 kB 3.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 7.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 22.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 8.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 11.8 MB/s eta 0:00:00
  Attempting uninstall: pyarrow
    Found existing installation: pyarrow 14.0.2
    Uninstalling pyarrow-14.0.2:
      Successfully uninstalled pyarrow-14.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf-cu12 24.4.1 requires pyarrow<15.0.0a0,>=14.0.1, but you have pyarrow 17.0.0 which is incompatible.
ibis-framework 8.0.0 requires pyarrow<16,>=2, but you have pyarrow 17.0.0 which is incompatible.


In [4]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer, Trainer, TrainingArguments
import torch

# Load the GPT-2 model and tokenizer
tokenizer = GPT2Tokenizer.from_pretrained('gpt2')
model = GPT2LMHeadModel.from_pretrained('gpt2')

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

In [ ]:
# Set the padding token for the tokenizer to be the end-of-sequence token
tokenizer.pad_token = tokenizer.eos_token

# Maximum sequence length that GPT-2 can handle
max_length = tokenizer.model_max_length
print(max_length)

1024


In [ ]:
from datasets import load_dataset

# Load the cleaned QA dataset as a training set using the 'datasets' library
dataset = load_dataset('csv', data_files={'train': 'cleaned_QA_data.csv'}, split='train')

In [ ]:
#Function to tokenize questions and answers and prepare them for the model
def tokenize_function(examples):

  '''1. Combine each question and answer into a single input string
     2. Tokenize the combined text using the GPT-2 tokenizer
     3. Set the labels to be the same as the input_ids (shifted to predict the next word)
     4. Return the tokenized output. '''

    combined_text = [str(q) + " " + str(a) for q, a in zip(examples['Questions'], examples['Answers'])]
    tokenized_output = tokenizer(combined_text, padding='max_length', truncation=True, max_length=128)

    tokenized_output['labels'] = tokenized_output['input_ids'].copy()

    return tokenized_output

Map:   0%|          | 0/118 [00:00<?, ? examples/s]

In [ ]:
# Tokenize the entire dataset
tokenized_dataset = dataset.map(tokenize_function, batched=True)

In [ ]:
# Define training arguments for the GPT-2 model
training_args = TrainingArguments(
    output_dir='./results', # Directory to save model outputs
    num_train_epochs=50, # Train for 50 epochs
    per_device_train_batch_size=16, # Batch size during training
    per_device_eval_batch_size=32, # Batch size during evaluation
    warmup_steps=500, # Warmup steps for learning rate scheduler
    weight_decay=0.01, # Weight decay for regularization
    logging_dir='./logs', # Directory for saving logs
    logging_steps=10, # Log every 10 steps
    save_steps=1000, # Save the model every 1000 steps
)

TrainOutput(global_step=400, training_loss=1.9328853976726532, metrics={'train_runtime': 206.7338, 'train_samples_per_second': 28.539, 'train_steps_per_second': 1.935, 'total_flos': 385405747200000.0, 'train_loss': 1.9328853976726532, 'epoch': 50.0})

In [ ]:
# Trainer class to handle training process
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_dataset,
    tokenizer=tokenizer,
)

In [ ]:
# Train the model
trainer.train()

In [ ]:
# Save the model
trainer.save_model('counsel_model')

In [7]:
# Function to generate a response based on a user prompt (testing the model)
def generate_response(prompt):
    inputs = tokenizer.encode(prompt, return_tensors="pt")
    outputs = model.generate(inputs, max_length=150, num_return_sequences=1, pad_token_id=tokenizer.eos_token_id)

    # Decode the generated output
    response = tokenizer.decode(outputs[0], skip_special_tokens=True)

    # Remove the prompt from the response
    if response.startswith(prompt):
        response = response[len(prompt):].strip()  # Remove the prompt from the response

    return response


In [9]:
# Example conversation
user_input = "How can I become a Data Scientist?"
bot_response = generate_response(user_input)
print("Bot Response:", bot_response)

Bot Response: Data scientists are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained to be data scientists. They are trained


In [ ]:
# Copying the model to Google Drive (optional)
import shutil

# Path to the file in Colab
colab_file_path = '/content/counsel_model/model.safetensors'

# Path to your Google Drive
drive_file_path = '/content/drive/MyDrive'

# Copy the file
shutil.copy(colab_file_path, drive_file_path)

'/content/drive/MyDrive/model.safetensors'